In [33]:
import glob, h5py, numpy,subprocess
from time import sleep
import os

In [34]:
fnames = glob.glob(
    '/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/*/*/HIGHSPIN_coinc/*HDFINJFIND*.hdf')

In [35]:
newnames = []
for n in fnames:
    newnames.append(n.split('runs/')[1])

In [36]:
newnames.sort()

In [37]:
finish = []
for new in newnames:
    finish.append(new.split('/HIGHSPIN_coinc')[0])

In [38]:
times = glob.glob('../inj-t10-1p4spin0p9/times/*.ini')

In [39]:
allrun = []
for t in times:
    obs = t.split('gps_times_')[1].split('_analysis')[0]
    chunk = t.split('_analysis_')[1].split('.')[0]
    allrun.append(obs+'/'+chunk)

In [40]:
allrun.sort()

In [41]:
unfinish = [item for item in allrun if item not in finish]

In [42]:
len(allrun),len(finish),len(unfinish)

(0, 84, 0)

In [27]:
unfinish

['O2/20',
 'O2/21',
 'O3/0',
 'O3/1',
 'O3/11',
 'O3/12',
 'O3/13',
 'O3/14',
 'O3/15',
 'O3/16',
 'O3/17',
 'O3/18',
 'O3/19',
 'O3/2',
 'O3/20',
 'O3/21',
 'O3/22',
 'O3/23',
 'O3/3',
 'O3/4',
 'O3/5',
 'O3/6',
 'O3/7',
 'O3/8',
 'O3/9',
 'O3b/1',
 'O3b/15',
 'O3b/17',
 'O3b/20',
 'O3b/22',
 'O3b/28',
 'O3b/7',
 'O3b/8']

In [30]:
for un in unfinish:
    print(un)
    a= glob.glob('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'+un+'/HIGHSPIN_coinc/H1L1V1-OPTIMAL_SNR_HIGHSPIN_INJECTIONS*.hdf')
    f = h5py.File(a[0],'r+')
    del f['optimal_snr']
    f.close()

O2/20
O2/21
O3/0
O3/1
O3/11
O3/12
O3/13
O3/14
O3/15
O3/16
O3/17
O3/18
O3/19
O3/2
O3/20
O3/21
O3/22
O3/23
O3/3
O3/4
O3/5
O3/6
O3/7
O3/8
O3/9
O3b/1
O3b/15
O3b/17
O3b/20
O3b/22
O3b/28
O3b/7
O3b/8


# Which PSD estimation is missing?

In [23]:
for unf in unfinish:
    basedir = '/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'
    for det in ['H1','L1','V1']:
        file = glob.glob(basedir+unf+'/HIGHSPIN_coinc/'+det+'-CALCULATE_PSD*.hdf')
        if len(file) == 0:
            print(unf,det,'PSD is missing')

# Great! All PSD estimation finished

# Let's work on hdfinjfind

In [24]:
def hdfinj_shfile(trigger,inj,veto,start_time,duration):
    c = "pycbc_coinc_hdfinjfind \
        --injection-window '2.0' \
        --optimal-snr-column H1:optimal_snr_H1 L1:optimal_snr_L1 V1:optimal_snr_V1 \
        --trigger-file %s \
        --injection-file %s \
        --veto-file %s \
        --segment-name closed_box \
        --output-file H1L1V1-HDFINJFIND_HIGHSPIN_INJECTIONS-%s-%s.hdf" % (str(trigger),str(inj),str(veto),str(start_time),str(duration))
    return c

In [25]:
for un in unfinish:
    pre = '/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'
    trigger = glob.glob(pre+un+'/HIGHSPIN_coinc/H1L1V1-COMBINE_STATMAP_HIGHSPIN_INJECTIONS-*.hdf')
    inj = glob.glob(pre+un+'/HIGHSPIN_coinc/H1L1V1-OPTIMAL_SNR_HIGHSPIN_INJECTIONS-*.hdf')
    veto = glob.glob(pre+un+'/local-scratch-dir/local-site-scratch/work/gw-main.dax_gw-main/H1L1V1-FOREGROUND_CENSOR-*.xml')
    if len(trigger)!=1 or len(inj)!= 1 or len(veto)!=1:
        print(un)
        raise RuntimeError('file doesnt exist or not matching!!')
    start = os.path.basename(trigger[0]).split('INJECTIONS-')[1].split('-')[0]
    duration = os.path.basename(trigger[0]).split('INJECTIONS-')[1].split('-')[1].split('.')[0]
    print(un,os.path.basename(trigger[0]),os.path.basename(inj[0]),veto[0],start,duration)
    contents = hdfinj_shfile(os.path.basename(trigger[0]),os.path.basename(inj[0]),veto[0],start,duration)
    with open('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'
                  +un+'/HIGHSPIN_coinc/hdfinjfind.sh','w') as f:
        f.write(contents)

O2/20 H1L1V1-COMBINE_STATMAP_HIGHSPIN_INJECTIONS-1185937218-687600.hdf H1L1V1-OPTIMAL_SNR_HIGHSPIN_INJECTIONS-1185937218-687600.hdf /work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/O2/20/local-scratch-dir/local-site-scratch/work/gw-main.dax_gw-main/H1L1V1-FOREGROUND_CENSOR-1185937218-687600.xml 1185937218 687600
O2/21 H1L1V1-COMBINE_STATMAP_HIGHSPIN_INJECTIONS-1186624818-687900.hdf H1L1V1-OPTIMAL_SNR_HIGHSPIN_INJECTIONS-1186624818-687900.hdf /work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/O2/21/local-scratch-dir/local-site-scratch/work/gw-main.dax_gw-main/H1L1V1-FOREGROUND_CENSOR-1186624818-687900.xml 1186624818 687900
O3/0 H1L1V1-COMBINE_STATMAP_HIGHSPIN_INJECTIONS-1238166018-533647.hdf H1L1V1-OPTIMAL_SNR_HIGHSPIN_INJECTIONS-1238166018-533647.hdf /work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/O3/0/local-scratch-dir/local-site-scratch/work/gw-main.dax_gw-main/H1L1V1-FOREGROUND_CENSOR-1238166018-533647.xml 1238166018 533647
O3/1 H1L1V1-COMBINE_STATMAP_HIGHS

O3b/28 H1L1V1-COMBINE_STATMAP_HIGHSPIN_INJECTIONS-1268764432-541460.hdf H1L1V1-OPTIMAL_SNR_HIGHSPIN_INJECTIONS-1268764432-541460.hdf /work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/O3b/28/local-scratch-dir/local-site-scratch/work/gw-main.dax_gw-main/H1L1V1-FOREGROUND_CENSOR-1268764432-541460.xml 1268764432 541460
O3b/7 H1L1V1-COMBINE_STATMAP_HIGHSPIN_INJECTIONS-1259855839-578036.hdf H1L1V1-OPTIMAL_SNR_HIGHSPIN_INJECTIONS-1259855839-578036.hdf /work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/O3b/7/local-scratch-dir/local-site-scratch/work/gw-main.dax_gw-main/H1L1V1-FOREGROUND_CENSOR-1259855839-578036.xml 1259855839 578036
O3b/8 H1L1V1-COMBINE_STATMAP_HIGHSPIN_INJECTIONS-1260433875-473178.hdf H1L1V1-OPTIMAL_SNR_HIGHSPIN_INJECTIONS-1260433875-473178.hdf /work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/O3b/8/local-scratch-dir/local-site-scratch/work/gw-main.dax_gw-main/H1L1V1-FOREGROUND_CENSOR-1260433875-473178.xml 1260433875 473178


In [31]:
len(unfinish)

33

In [32]:
for un in unfinish:
    print(un)
    os.chdir('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'
                  +un+'/HIGHSPIN_coinc/')
    subprocess.run(['bash','hdfinjfind.sh'])

O2/20
O2/21
O3/0
O3/1
O3/11
O3/12
O3/13
O3/14
O3/15
O3/16
O3/17
O3/18
O3/19
O3/2
O3/20
O3/21
O3/22
O3/23
O3/3
O3/4
O3/5
O3/6
O3/7
O3/8
O3/9
O3b/1
O3b/15
O3b/17
O3b/20
O3b/22
O3b/28
O3b/7
O3b/8


# Let's work on combine statmap

In [54]:
def combine_shfile(fstatmap,fbackground,start_time,duration):
    c = "pycbc_add_statmap --cluster-window '10.0' \
        --statmap-files %s \
        --output-file H1L1V1-COMBINE_STATMAP_HIGHSPIN_INJECTIONS-%s-%s.hdf  \
        --background-files ../full_data/%s" % (str(fstatmap),str(start_time),str(duration),str(fbackground))
    return c

In [55]:
for un in unfinish:
    fstatmap = glob.glob('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'+un+'/HIGHSPIN_coinc/H1L1V1-STATMAP_INJ_HIGHSPIN_INJECTIONS_*.hdf')
    fbackground = glob.glob('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'+un+'/full_data/H1L1V1-STATMAP_FULL_DATA_3DET-*.hdf')
    if len(fstatmap) is not 1 or len(fbackground) is not 1:
        raise RuntimeError('file doesnt exist or not matching!!')
    start = os.path.basename(fbackground[0]).split('3DET-')[1].split('-')[0]
    duration = os.path.basename(fbackground[0]).split('3DET-')[1].split('-')[1].split('.')[0]
    print(un,os.path.basename(fstatmap[0]),os.path.basename(fbackground[0]),start,duration)
    contents = combine_shfile(os.path.basename(fstatmap[0]),os.path.basename(fbackground[0]),start,duration)
    with open('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'
                  +un+'/HIGHSPIN_coinc/combinestatmap.sh','w') as f:
        f.write(contents)

O2/20 H1L1V1-STATMAP_INJ_HIGHSPIN_INJECTIONS_3DET_VETOES-1185937218-687600.hdf H1L1V1-STATMAP_FULL_DATA_3DET-1185937218-687600.hdf 1185937218 687600
O2/21 H1L1V1-STATMAP_INJ_HIGHSPIN_INJECTIONS_3DET_VETOES-1186624818-687900.hdf H1L1V1-STATMAP_FULL_DATA_3DET-1186624818-687900.hdf 1186624818 687900
O3/0 H1L1V1-STATMAP_INJ_HIGHSPIN_INJECTIONS_3DET_VETOES-1238166018-533647.hdf H1L1V1-STATMAP_FULL_DATA_3DET-1238166018-533647.hdf 1238166018 533647
O3/1 H1L1V1-STATMAP_INJ_HIGHSPIN_INJECTIONS_3DET_VETOES-1238699665-713196.hdf H1L1V1-STATMAP_FULL_DATA_3DET-1238699665-713196.hdf 1238699665 713196
O3/11 H1L1V1-STATMAP_INJ_HIGHSPIN_INJECTIONS_3DET_VETOES-1244799444-699937.hdf H1L1V1-STATMAP_FULL_DATA_3DET-1244799444-699937.hdf 1244799444 699937
O3/12 H1L1V1-STATMAP_INJ_HIGHSPIN_INJECTIONS_3DET_VETOES-1245499381-760256.hdf H1L1V1-STATMAP_FULL_DATA_3DET-1245499381-760256.hdf 1245499381 760256
O3/13 H1L1V1-STATMAP_INJ_HIGHSPIN_INJECTIONS_3DET_VETOES-1246259637-1082491.hdf H1L1V1-STATMAP_FULL_DATA_3DE

In [56]:
for un in unfinish:
    print(un)
    os.chdir('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'
                  +un+'/HIGHSPIN_coinc/')
    subprocess.run(['bash','combinestatmap.sh'])

O2/20
O2/21
O3/0
O3/1
O3/11
O3/12
O3/13
O3/14
O3/15
O3/16
O3/17
O3/18
O3/19
O3/2
O3/20
O3/21
O3/22
O3/23
O3/3
O3/4
O3/5
O3/6
O3/7
O3/8
O3/9
O3b/1
O3b/15
O3b/17
O3b/20
O3b/22
O3b/28
O3b/7
O3b/8


# Let's work on optimal SNR

In [13]:
def osnr_shfile(start_time,duration):
    c = "pycbc_optimal_snr \
        --snr-columns H1:optimal_snr_H1 L1:optimal_snr_L1 V1:optimal_snr\
        --f-low '10'  \
        --seg-length '512' \
        --sample-rate '2048' \
        --cores '1' \
        --input-file ../inj_highspin_mass1p4_dist20_300.hdf \
        --injection-fraction-range 0/1 \
        --time-varying-psds H1-CALCULATE_PSD_PART0-%s-%s.hdf L1-CALCULATE_PSD_PART0-%s-%s.hdf V1-CALCULATE_PSD_PART0-%s-%s.hdf  \
        --output-file H1L1V1-OPTIMAL_SNR_HIGHSPIN_INJECTIONS-%s-%s.hdf" % (str(start_time),str(duration),str(start_time),str(duration),
                                                                           str(start_time),str(duration),str(start_time),str(duration))
    return c

def osnr_subfile():
    c = 'universe = vanilla \n'+\
    'accounting_group = cbc.imp.pe \n'+\
    'getenv = True \n'+\
    'executable = /bin/bash \n\
arguments = optimalsnr.sh \n\
output = snrcondor.output  \n\
error = snrcondor.error   \n\
log = snrcondor%s.log \n\
request_cpus = 1 \n\
request_memory = 8000 \n\
notification = Complete \n\
notify_user = yifan.wang@aei.mpg.de \n\
queue'
    return c

In [27]:
unfinish.remove('O2/2')
unfinish.remove('O2/15')

ValueError: list.remove(x): x not in list

In [28]:
unfinish

['O2/20',
 'O2/21',
 'O3/0',
 'O3/1',
 'O3/11',
 'O3/12',
 'O3/13',
 'O3/14',
 'O3/15',
 'O3/16',
 'O3/17',
 'O3/18',
 'O3/19',
 'O3/2',
 'O3/20',
 'O3/21',
 'O3/22',
 'O3/23',
 'O3/3',
 'O3/4',
 'O3/5',
 'O3/6',
 'O3/7',
 'O3/8',
 'O3/9',
 'O3b/1',
 'O3b/15',
 'O3b/17',
 'O3b/20',
 'O3b/22',
 'O3b/28',
 'O3b/7',
 'O3b/8']

In [30]:
unfinish.remove('O2/2')
unfinish.remove('O2/15')
for un in unfinish:
#un = unfinish[0]
    psds = glob.glob('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'+un+'/HIGHSPIN_coinc/*CALCULATE_PSD_PART0*.hdf')
    if len(psds) is not 3:
        print(un)
        raise RuntimeError("PSD is incomplete")
    psd = psds[0].split('CALCULATE_PSD_PART0-')[1]
    start_time = psd.split('-')[0]
    duration = psd.split('-')[1].split('.')[0]
    contents = osnr_shfile(start_time,duration)
    with open('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'
                  +un+'/HIGHSPIN_coinc/optimalsnr.sh','w') as f:
        f.write(contents)

# Write a snrsub

In [18]:
os.chmod

<function posix.chmod(path, mode, *, dir_fd=None, follow_symlinks=True)>

In [21]:
for un in unfinish:
    print(un)
    contents = osnr_subfile()
    with open('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'
                  +un+'/HIGHSPIN_coinc/osnr_sub.sub','w') as f:
        f.write(contents)
    os.chdir('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'
                  +un+'/HIGHSPIN_coinc/')
    subprocess.run(['condor_submit','osnr_sub.sub'])
    sleep(5)

O2/15
Submitting job(s).
1 job(s) submitted to cluster 5067815.
O2/2
Submitting job(s).
1 job(s) submitted to cluster 5067816.
O2/20
Submitting job(s).
1 job(s) submitted to cluster 5067817.
O2/21
Submitting job(s).
1 job(s) submitted to cluster 5067818.
O3/0
Submitting job(s).
1 job(s) submitted to cluster 5067819.
O3/1
Submitting job(s).
1 job(s) submitted to cluster 5067820.
O3/11
Submitting job(s).
1 job(s) submitted to cluster 5067821.
O3/12
Submitting job(s).
1 job(s) submitted to cluster 5067822.
O3/13
Submitting job(s).
1 job(s) submitted to cluster 5067823.
O3/14
Submitting job(s).
1 job(s) submitted to cluster 5067824.
O3/15
Submitting job(s).
1 job(s) submitted to cluster 5067825.
O3/16
Submitting job(s).
1 job(s) submitted to cluster 5067826.
O3/17
Submitting job(s).
1 job(s) submitted to cluster 5067827.
O3/18
Submitting job(s).
1 job(s) submitted to cluster 5067828.
O3/19
Submitting job(s).
1 job(s) submitted to cluster 5067829.
O3/2
Submitting job(s).
1 job(s) submitted 

In [136]:
def dataframe(run,chunk,ifo):
    if run == 'O1':
        frame = ifo + '_LOSC_16_V1'
        channel = ifo + ':GWOSC-16KHZ_R1_STRAIN'
        
    elif run == 'O2' and chunk == '15p':
        if ifo == 'H1':
            frame = ifo + '_GWOSC_BKGW170608_16KHZ_R1'
        elif ifo == 'L1':
            frame = ifo + '_GWOSC_O2_16KHZ_R1'
        channel = ifo + ':GWOSC-16KHZ_R1_STRAIN'
        
    elif run == 'O2' and int(chunk) <= 18: 
        frame = ifo + '_GWOSC_O2_16KHZ_R1'
        channel = ifo + ':GWOSC-16KHZ_R1_STRAIN'
        
    elif run == 'O2' and int(chunk) >= 19: 
        frame = ifo + '_GWOSC_O2_16KHZ_R1'
        channel = ifo + ':GWOSC-16KHZ_R1_STRAIN'
        
    elif run == 'O3':
        frame = ifo + '_GWOSC_O3a_4KHZ_R1'
        channel = ifo + ':GWOSC-4KHZ_R1_STRAIN'
        
    elif run == 'O3b':
        frame = ifo + '_GWOSC_O3b_4KHZ_R1'
        channel = ifo + ':GWOSC-4KHZ_R1_STRAIN'
    return frame,channel

def shfile(frame,channel,xmlfile,output):
    c = "pycbc_calculate_psd \
    --cores 32 --low-frequency-cutoff '10' \
    --pad-data '2' --strain-high-pass '9' --sample-rate '2048' \
    --segment-length '512' --segment-start-pad '300' --segment-end-pad '16' \
    --psd-estimation median --psd-segment-length '16' --psd-segment-stride '8' \
    --psd-num-segments '63' --taper-data '1' --autogating-threshold '25' \
    --autogating-cluster '0.25' --autogating-width '0.125' \
    --autogating-taper '0.125' --autogating-pad '16' \
    --frame-type %s \
    --channel-name %s \
    --analysis-segment-file %s \
    --segment-name DATA_ANALYSED \
    --output-file %s" % (frame,channel,xmlfile,output)
    return c

def subfile(ifo):
    c = 'universe = vanilla \n'+\
    'accounting_group = cbc.imp.post-processing \n'+\
    'getenv = True \n'+\
    'executable = /bin/bash \n\
arguments = psd%s.sh \n\
output = condor%s.output  \n\
error = condor%s.error   \n\
log = condor%s.log \n\
request_cpus = 32 \n\
request_memory = 80000 \n\
notification = Complete \n\
notify_user = yifan.wang@aei.mpg.de \n\
queue' % (ifo,ifo,ifo,ifo)
    return c

In [137]:
"a\n%s\
b" % ('ifo')

'a\nifob'

In [138]:
dataframe('O3','15','V1')

('V1_GWOSC_O3a_4KHZ_R1', 'V1:GWOSC-4KHZ_R1_STRAIN')

In [139]:
un

'O2/15'

In [140]:
un.split('/')

['O2', '15']

In [141]:
subfile('H1')

'universe = vanilla \naccounting_group = cbc.imp.post-processing \ngetenv = True \nexecutable = /bin/bash \narguments = psdH1.sh \noutput = condorH1.output  \nerror = condorH1.error   \nlog = condorH1.log \nrequest_cpus = 32 \nrequest_memory = 80000 \nnotification = Complete \nnotify_user = yifan.wang@aei.mpg.de \nqueue'

In [147]:
unfinish.remove('O2/15')

In [148]:
unfinish

['O2/2',
 'O2/20',
 'O2/21',
 'O3/0',
 'O3/1',
 'O3/11',
 'O3/12',
 'O3/13',
 'O3/14',
 'O3/15',
 'O3/16',
 'O3/17',
 'O3/18',
 'O3/19',
 'O3/2',
 'O3/20',
 'O3/21',
 'O3/22',
 'O3/23',
 'O3/3',
 'O3/4',
 'O3/5',
 'O3/6',
 'O3/7',
 'O3/8',
 'O3/9',
 'O3b/1',
 'O3b/15',
 'O3b/17',
 'O3b/20',
 'O3b/22',
 'O3b/28',
 'O3b/7',
 'O3b/8']

In [150]:
for un in unfinish:
#un = unfinish[0]
    psds = glob.glob('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'+un+'/psds/*.xml')
    for psd in psds:
        ifo = psd.split('-DATA_ANALYSED_')[0][-2:]
        run = un.split('/')[0]
        chunk = un.split('/')[1]
        print(run,chunk,ifo)
        frame,channel = dataframe(run,chunk,ifo)
        num1 = psd.split('DATA_ANALYSED_0-')[1].split('-')[0]
        num2 = psd.split('DATA_ANALYSED_0-')[1].split('-')[1].split('.')[0]
        output = ifo + '-CALCULATE_PSD_PART0-' + num1 + '-' + num2 + '.hdf'
        contents = shfile(frame,channel,psd,output)
        subfilecontents = subfile(ifo)
        with open('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'
                  +run+'/'+chunk+'/HIGHSPIN_coinc/psd'+ifo+'.sh','w') as f:
            f.write(contents)
        with open('/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'
                  +run+'/'+chunk+'/HIGHSPIN_coinc/sub'+ifo+'.sub','w') as f:
            f.write(subfilecontents)
        subprocess.run(['condor_submit','/work/yifan.wang/search-high-spin/inj-t10-1p4spin0p9/runs/'\
                  +run+'/'+chunk+'/HIGHSPIN_coinc/sub'+ifo+'.sub'])
        sleep(5)

O2 2 L1
Submitting job(s).
1 job(s) submitted to cluster 5061447.
O2 2 H1
Submitting job(s).
1 job(s) submitted to cluster 5061448.
O2 20 V1
Submitting job(s).
1 job(s) submitted to cluster 5061449.
O2 20 H1
Submitting job(s).
1 job(s) submitted to cluster 5061450.
O2 20 L1
Submitting job(s).
1 job(s) submitted to cluster 5061451.
O2 21 L1
Submitting job(s).
1 job(s) submitted to cluster 5061452.
O2 21 H1
Submitting job(s).
1 job(s) submitted to cluster 5061453.


KeyboardInterrupt: 